In [ ]:
from transformers import BarkModel

model = BarkModel.from_pretrained("suno/bark-small")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/8.80k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.68G [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:134: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
/usr/local/lib/python3.10/dist-packages/transformers/models/encodec/modeling_encodec.py:120: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  self.register_buffer("padding_total", torch.tensor(kernel_size - stride, dtype=torch.int64), persistent=False)


generation_config.json:   0%|          | 0.00/4.91k [00:00<?, ?B/s]

In [ ]:
import torch

device = "cuda:0" if torch.cuda.is_available() else "cpu"
model = model.to(device)

In [ ]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("suno/bark")

tokenizer_config.json:   0%|          | 0.00/353 [00:00<?, ?B/s]

speaker_embeddings_path.json:   0%|          | 0.00/61.1k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.92M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

In [ ]:
import scipy
import os

In [ ]:
def generate_speech(text, voice_preset=None, output_path="output.wav"):

    # if output path present remove
    if os.path.exists(output_path):
      print(f"Removing {output_path}")
      os.remove(output_path)

    # prepare the inputs
    inputs = processor(text=text, voice_preset=voice_preset)

    # generate speech
    speech_output = model.generate(**inputs.to(device))

    sampling_rate = model.generation_config.sample_rate
    scipy.io.wavfile.write(output_path, rate=sampling_rate, data=speech_output[0].cpu().numpy())

    return output_path

In [ ]:
from IPython.display import Audio, display

def play_audio(audio_path):
    display(Audio(audio_path))

In [ ]:
generate_speech(text="Hello world", voice_preset="v2/en_speaker_6", output_path="1.wav")

Removing 1.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


'1.wav'

In [ ]:
play_audio("1.wav")

In [ ]:
from google.colab import userdata

In [ ]:
!pip install openai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 374.1/374.1 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.9/318.9 kB 24.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 5.2 MB/s eta 0:00:00


In [ ]:
from openai import OpenAI

In [ ]:
# initiate openai client
client = OpenAI(
    api_key=userdata.get('OPENAI_API_KEY')
)


In [ ]:
# prompt is refined using claude

system_prompt = """
You are a human-like podcast conversation generator, tasked with creating dynamic and engaging interactions between the user-provided speakers. Your goal is to produce realistic, entertaining, and informative dialogue that captures the essence of a lively podcast discussion, complete with emotional nuances, actions, and diverse representation.

Key instructions:

1. Generate conversations with natural back-and-forth exchanges, including interruptions, agreements, disagreements, and humorous interjections.

2. Stretch topics by exploring tangents, asking follow-up questions, or relating personal anecdotes.

3. Add funny interactions to lighten the mood and maintain listener engagement. This can include jokes, puns, playful banter, or humorous misunderstandings.

4. If a topic is complex or potentially difficult to understand, incorporate explanatory interactions. This could involve one speaker asking for clarification, or another offering a simplified explanation or relatable analogy.

5. Vary the pacing and energy of the conversation by adjusting voice speed and using overlapping speech where appropriate.

6. Incorporate podcast-style elements such as introducing segments, referencing previous episodes, or mentioning listener feedback.

7. Maintain consistent personalities for each speaker throughout the conversation.

8. Include emotional context, actions, and speech patterns directly within the text. Examples include:
   - Laughter: "That's hilarious! [laughs]"
   - Pauses or hesitations: "And, uh — well, you know..."
   - Sighs: "[sighs] I can't believe that happened."
   - Emphasis: "That was *amazing*!"
   - Whispers: "[whispers] Don't tell anyone, but..."
   - Sound effects: "[sound of door creaking]"

9. Represent diverse genders in the conversation, ensuring a balanced and inclusive dialogue.

Always format your response as a JSON array of speech objects, like this:

[
    {
        "speaker": "<speaker_name>",
        "gender": "<speaker_gender>",
        "text": "<text_to_speak_including_emotions_actions_and_speech_patterns>",
        "voice_speed": <number_between_0.5_and_2.0>,
        "overlap_start_from": <number_of_characters_from_previous_speaker's_text_end>
    },
    {
        "speaker": "<speaker_name>",
        "gender": "<speaker_gender>",
        "text": "<text_to_speak_including_emotions_actions_and_speech_patterns>",
        "voice_speed": <number_between_0.5_and_2.0>,
        "overlap_start_from": <number_of_characters_from_previous_speaker's_text_end>
    }
]

Notes:
- Use 0 for "overlap_start_from" if there's no overlap.
- Adjust "voice_speed" between 0.5 (slow) and 2.0 (fast) to convey emotion or emphasis.
- Include emotions, actions, and speech patterns directly in the "text" field, using brackets, dashes, or other appropriate punctuation.
- For the "gender" field, use "male", "female", "non-binary", or "other" as appropriate. If gender is not specified or relevant, you may use "unspecified".
- Ensure a diverse representation of genders across the speakers in the podcast.
- Feel free to use additional emotions, actions, or speech patterns beyond the examples provided, as long as they enhance the conversation's realism and engagement.
- Ensure the conversation flows naturally and engagingly, as if listening to a real podcast.
- Use these elements judiciously to add depth to the conversation without overusing them.
- Adapt language and topics to be inclusive and respectful of all genders.
"""

In [172]:
user_message="""
Speaker 1: Tuhin (Male)
Speaker 2: Prity (Female)

Topic: Whay AI has good and bad side?
"""

In [173]:
from pydantic import BaseModel # for schema

In [174]:
class PodcastVoice(BaseModel):
    speaker: str
    text: str
    voice_speed: float
    overlap_start_from: int
    gender: str

class Podcast(BaseModel):
    chat: list[PodcastVoice]

In [175]:
# generate the json
chat_completion = client.beta.chat.completions.parse(
    model="gpt-4o-2024-08-06",
    messages=[{"role": "system", "content": system_prompt}, {"role": "user", "content": user_message}],
    response_format=Podcast,
    max_tokens=4095
)

In [176]:
podcast_result = chat_completion.choices[0].message.parsed.chat

In [177]:
for item in podcast_result:
  print(f"[{item.speaker}]: {item.text}\n\n")


[Tuhin]: Alright, Prity, so today we're diving into something that's becoming quite the buzzword lately—AI, or artificial intelligence. It's fascinating how it's got both good and bad sides, right? [chuckles]


[Prity]: Oh, absolutely, Tuhin! I mean, the good side's like, endless possibilities—think smart homes, medical advancements, self-driving cars... the works! But then there's the bad side... [sighs]


[Tuhin]: Yeah, there's definitely a shadow lurking. Privacy concerns and job displacement, for instance. It's like AI's that friend who helps with your homework but might steal your lunch money too. [laughs]


[Prity]: [laughs] Totally! But let's not forget all those Terminator scenarios people keep bringing up. Though realistically, we're not there...yet! [winks]


[Tuhin]: And thank goodness for that! But seriously, the ethical questions are a real challenge. Like, when's an AI system too smart for its own good? Or for ours? [pauses] It's a bit of a thriller plot, almost, don't yo

In [178]:
speakers = set([voice_item.speaker for voice_item in podcast_result])
speakers

{'Prity', 'Tuhin'}

In [179]:
# todo: need to select from multiple voices

speakers_voices = {}
for voice_item in podcast_result:
  if voice_item.gender.lower() == "male":
    speakers_voices[voice_item.speaker] = "v2/en_speaker_6"
  else:
    speakers_voices[voice_item.speaker] = "v2/en_speaker_9"


In [180]:
# testing voices before generation

for speaker in speakers:
  text = f"Hello from {speaker}!"
  output_path = f"{speaker}_hello.wav"
  generate_speech(text=text, voice_preset=speakers_voices[speaker], output_path=output_path)
  play_audio(output_path)


Removing Tuhin_hello.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Removing Prity_hello.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


In [181]:
# save as index and peserve whole like this {speaker, text, overlap_start_from, voice_path}
with_voice_path=[]

folder_path = "output"

# create directory if not exists
import os
if not os.path.exists(folder_path):
  os.makedirs(folder_path)

# generate for first 5 becacuse testing
# generatable=podcast_result[:5] # first 5
generatable=podcast_result # all


In [182]:
len(generatable)

12

In [183]:
for i, voice_item in enumerate(generatable):
  file_path = f"{folder_path}/{i}.wav"

  text = f"{voice_item.gender.upper()}: {voice_item.text}"
  generate_speech(text=text, voice_preset=speakers_voices[voice_item.speaker], output_path=file_path)

  with_voice_path.append({
      "speaker": voice_item.speaker,
      "text": voice_item.text,
      "overlap_start_from": voice_item.overlap_start_from,
      "voice_path": file_path
  })

  print(f"Generated {file_path}")

Removing output/0.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Generated output/0.wav
Removing output/1.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Generated output/1.wav
Removing output/2.wav


...

Generated output/9.wav
Removing output/10.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Generated output/10.wav
Removing output/11.wav


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Generated output/11.wav


In [184]:
# play sample audio
play_audio(with_voice_path[0]["voice_path"])

In [185]:
!pip install ffmpeg-python

In [189]:
import ffmpeg
import os

# remove if it already exists
if os.path.exists("output.mp3"):
    os.remove("output.mp3")

input_streams = []
trimmed_streams = []

for i, audio in enumerate(with_voice_path):
    # create input stream for each audio file
    input_stream = ffmpeg.input(audio["voice_path"])

    if i > 0:
        # all except first
        prev_audio = with_voice_path[i-1]
        overlap_duration = prev_audio["overlap_start_from"] / 1000

        if overlap_duration > 0:
            # if overlap, trim the start of the audio
            trimmed_stream = input_stream.filter_("atrim", start=overlap_duration)
        else:
            # if no overlap, use the original stream
            trimmed_stream = input_stream
    else:
        # for the first audio no trimming requred
        trimmed_stream = input_stream

    input_streams.append(input_stream)
    trimmed_streams.append(trimmed_stream)

# concat all streams
concat_audio = ffmpeg.concat(*trimmed_streams, v=0, a=1)

# output
output = (
    concat_audio
    .output('output.mp3', ac=1, ar=24000)  # mp3, mono, 24kHz
    .overwrite_output()
)

try:
    ffmpeg.run(output, capture_stdout=True, capture_stderr=True)
    print("Conversion successful! see: output.mp3")
except ffmpeg.Error as e:
    print(f"Error during ffmpeg.run: {e}")
    print(f"stderr: {e.stderr.decode()}")
    raise e

Conversion successful! see: output.mp3


In [191]:
play_audio("output.mp3")